# A Trajectory Analysis using the ICESat2 Satellite

For information on adding the ICESat2 satellite to `pygeodyn` see the notebook titled, *Adding a New Satellite: ICESat2*.



## Step 1:  Pre-processing the PCE data into a G2B file

We will construct a `G2B_PCE`file from a set of binary `.rvg` files which contain trajectory output from a reduced-dynamics run of GEODYN. The files will be stitched together to create a the GEODYN-specific, trajectory-based tracking data type (called PCE (Precice-Clock-Error) ) and stored in a G2B file.

Each `.rvg` file contains a **30-hour arc of ICESat2 trajectory data**.  These datasets are the output from a very precise run of GEODYN in which the orbit has been determined very well (*to a few centimeters accuracy*) using a **reduced dynamics technique** (*empirical accelerations and other parameters are adjusted to account for any mismodelled forces)*.

The process that takes place in `pygeodyn` is as follows:
  1. dump the data from each arc into a usable format
  2. chop of the 3 hour padding on the ends to eliminate discontinuities from end effects
  3. stitch together all the files
  4. smooth over any existing discontinuities between arc gaps or maneuvers.
  5. All data is placed in a single `TRAJ.txt` file which is then fed into a Fortran script (`pce_converer.f`) which converts the data into a `G2B` file to be ingested on `fort.40` of the GEODYN run.

### PygeodynPreprocessing


In [1]:
%load_ext autoreload
%autoreload 2

import sys
sys.path.insert(0,'/data/geodyn_proj/pygeodyn/utils_pygeodyn_develop/util_preprocessing/')
from PYGEODYN_Preprocess import PygeodynPreprocessing

path_to_prep_directory = '/data/data_geodyn/inputs/icesat2/pre_processing'
path_to_binaryrvg     = '/data/data_geodyn/inputs/icesat2/pre_processing/traj_files_rvg'

arc1_files = ['orbit.1807001.2018.287']
# arc1_files = ['orbit.1807001.2018.312',
#             'orbit.1807001.2018.313',
#             'orbit.1807001.2018.314',
#             'orbit.1807001.2018.315',
#             'orbit.1807001.2018.316',
#             'orbit.1807001.2018.317',
#             'orbit.1807001.2018.318',
#             'orbit.1807001.2018.319',
#             'orbit.1807001.2018.320',
#             'orbit.1807001.2018.321',
#             'orbit.1807001.2018.322',
#             'orbit.1807001.2018.323',
#             'orbit.1807001.2018.324',
#             'orbit.1807001.2018.325',
#             'orbit.1807001.2018.326',
#             'orbit.1807001.2018.327',
#             'orbit.1807001.2018.328',
#              ]


# Obj = PygeodynPreprocessing(path_to_binaryrvg, path_to_prep_directory,  arc1_files)
# Obj.run_preprocess_PCE()


## Use pygeodyn to run GEODYN with the ICESat2 configuration

<!-- The gzipped `g2b` file must be placed in the proper directory.
 -->
 
 


In [2]:
%load_ext autoreload
%autoreload 2

sys.path.insert(0, '/data/geodyn_proj/pygeodyn/utils_pygeodyn_develop/')
from PYGEODYN import Pygeodyn

#------ A dictionary containing the run parameters ------  
run_params = {} 
run_params['run_ID']           =  'Run_Arc_1'  
run_params['arc']              =  'iisset.2018.287'
run_params['satellite']        =  'icesat2'  
run_params['den_model']        =  'msis2'  
run_params['empirical_accels'] =  False  
run_params['SpecialRun_name']  =  '_developer_test'  
run_params['options_in']       =  {'DRHODZ_update':True}  
run_params['verbose']          =  False
run_params['action']           =   'run'



Obj_Geodyn = Pygeodyn(run_params)
Obj_Geodyn.RUN_GEODYN()

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
   Initializing PYGEODYN to ... 
                            ... RUN GEODYN
Run_Arc_1     Current Time =      23:10:15

Run_Arc_1     Cleaning iisset:    /data/data_geodyn/inputs/icesat2/setups/iisset.2018.287
Run_Arc_1     This run's iisset:  /data/data_geodyn/inputs/icesat2/setups/cleaned_setup_file
Run_Arc_1     Density Model:      msis2
Run_Arc_1     GEODYN Version:     pygeodyn_MODS
Run_Arc_1     Estimate GenAccel:  acceloff
Run_Arc_1     ARC run:            iisset.2018.287
Run_Arc_1     Output directory:   /data/data_geodyn/results/icesat2/msis2/msis2_acceloff_developer_test
Run_Arc_1     Call Options:       {'DRHODZ_update': True}
Run_Arc_1     EXAT File:     /data/data_geodyn/inputs/icesat2/external_attitude/EXAT01.2018.287.gz

Run_Arc_1          Running IIS
Run_Arc_1          No errors in IIS
Run_Arc_1 ---------End of IIS

Run_Arc_1          Running IIE
Run_Arc_1          Current Time = 23:

In [3]:
Obj_Geodyn = Pygeodyn(run_params)

Obj_Geodyn.getData_Arc()

   Initializing PYGEODYN to ... 
                            ... RUN GEODYN
        
     File path: 
     Loading /data/data_geodyn/results/icesat2/msis2/msis2_acceloff_developer_test/.../iisset.2018.287 
[   2    3    4 ... 7091 7092 7093]
DatetimeIndex(['2018-10-14 06:00:00', '2018-10-14 15:00:00',
               '2018-10-15 00:00:00', '2018-10-15 09:00:00',
               '2018-10-15 18:00:00', '2018-10-16 03:00:00'],
              dtype='datetime64[ns]', freq=None)


In [4]:
import plotly.graph_objects as go
import numpy as np
from plotly.offline import plot, iplot
from plotly.subplots import make_subplots
import plotly.express as px
import copy
import sys  
import numpy as np


config = dict({
                'displayModeBar': True,
                'responsive': False,
#                 'staticPlot': True,
                'displaylogo': False,
                'showTips': False,
                })

In [8]:
%load_ext autoreload
%autoreload 2
from pygeodyn_Analysis import plot_residuals_observed
from funcs_plotting_scheme import help_plot_colors, add_arc_background_w_text, legend_as_annotation
col1, col2, col3 = help_plot_colors()


obj_m1 = Obj_Geodyn
fig = make_subplots(rows=1, cols=1, 
#         subplot_titles=(['Orbit Averaged Density', 'Ap', 'F10.7']),
#          horizontal_spacing = 0.05,
#          vertical_spacing = 0.1,
                   )
plot_num = 0

arc_list = [obj_m1.__dict__['run_parameters']['arc_input']]
model_m1 = obj_m1.__dict__['run_parameters']['den_model']
# iter_list = [' 1' , obj_m1.__dict__['run_parameters']['str_iteration']]
iter_list = [ obj_m1.__dict__['run_parameters']['str_iteration']]

if plot_num == 0:
    col = col1
    x_annot = 1.05
    y_annot = .9
elif plot_num == 1:
    x_annot = 1.05
    y_annot = .8
    col = col2
elif plot_num == 2:
    x_annot = 1.05
    y_annot = .7 
    col = col3    

for ii, i_iter in enumerate(iter_list): 
    
    if ii==0:
        m_size = 3
    elif ii==1:
        m_size = 3
        
    for i,arc in enumerate(arc_list):
        i_arc = i+1


        index_pce_x = obj_m1.Residuals_obs[arc][i_iter]['StatSatConfig'] == 'PCE X    '
        index_pce_y = obj_m1.Residuals_obs[arc][i_iter]['StatSatConfig'] == 'PCE Y    '
        index_pce_z = obj_m1.Residuals_obs[arc][i_iter]['StatSatConfig'] == 'PCE Z    '

        fig.add_trace(go.Scattergl(x=obj_m1.Residuals_obs[arc][i_iter]['Date'][index_pce_x][::3],
                                 y=obj_m1.Residuals_obs[arc][i_iter]['Residual'][index_pce_x][::3],
                                 name= 'PCE X',
                                 mode='markers',
                                 marker=dict(color=col1,
                                 size=m_size,),
                                 showlegend=True,
                                 ),
                                 )
        fig.add_trace(go.Scattergl(x=obj_m1.Residuals_obs[arc][i_iter]['Date'][index_pce_y][::3],
                                 y=obj_m1.Residuals_obs[arc][i_iter]['Residual'][index_pce_y][::3],
                                 name= 'PCE Y',
                                 mode='markers',
                                 marker=dict(color=col2,
                                 size=m_size,),
                                 showlegend=True,
                                 ),
                                 )

        fig.add_trace(go.Scattergl(x=obj_m1.Residuals_obs[arc][i_iter]['Date'][index_pce_z][::3],
                                 y=obj_m1.Residuals_obs[arc][i_iter]['Residual'][index_pce_z][::3],
                                 name= 'PCE Z',
                                 mode='markers',
                                 marker=dict(color=col3,
                                 size=m_size,),
                                 showlegend=True,
                                 ),
                                 )
    #     fig = add_arc_background_w_text(fig, 1.1*np.max(obj_m1.Residuals_obs[arc]['Residual'] ), arc_list, False)


# fig.update_yaxes(type="log", exponentformat= 'power')

fig.update_layout(
    title='Observation Residuals',
    yaxis_title="Residuals",
    xaxis_title="Date",
    )
fig.update_layout(legend= {'itemsizing': 'constant'})
fig.update_layout(
    font=dict(size=17))
# iplot(fig) 
# iplot(fig)
fig.show(config=config)


The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
